# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# less than 10 documents,
id2word = corpora.Dictionary(data)
id2word.filter_extremes(no_below = 10)

In [11]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [12]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [13]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [14]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [15]:
ldaseq.print_topics(time=0) # at timeslice 1, those are the topics

[[('method', 0.042398018104208006),
  ('function', 0.03704571163734502),
  ('algorithm', 0.03642388659444472),
  ('problem', 0.024844984578497518),
  ('gradient', 0.02235592641944609),
  ('optimization', 0.02041294510246423),
  ('convergence', 0.01637484360608393),
  ('convex', 0.01601229519726301),
  ('loss', 0.014449336938062933),
  ('learning', 0.014398634467997558),
  ('stochastic', 0.011491393465665557),
  ('descent', 0.01053788694709844),
  ('rate', 0.009427969079292447),
  ('objective', 0.009044526284691129),
  ('show', 0.008743000509709133),
  ('paper', 0.00728675499728591),
  ('result', 0.006284884589465521),
  ('iteration', 0.006138723797466128),
  ('proposed', 0.006024407001071116),
  ('local', 0.005867306536694031)],
 [('algorithm', 0.023964009191690543),
  ('problem', 0.023929039796840468),
  ('policy', 0.016762517529938323),
  ('learning', 0.015611155917657478),
  ('state', 0.01179478987417689),
  ('function', 0.011585756577039613),
  ('show', 0.01049761602645038),
  ('de

In [16]:
ldaseq.print_topic_times(topic=0) # evolution of 1st topic through all timeslices

[[('method', 0.042398018104208006),
  ('function', 0.03704571163734502),
  ('algorithm', 0.03642388659444472),
  ('problem', 0.024844984578497518),
  ('gradient', 0.02235592641944609),
  ('optimization', 0.02041294510246423),
  ('convergence', 0.01637484360608393),
  ('convex', 0.01601229519726301),
  ('loss', 0.014449336938062933),
  ('learning', 0.014398634467997558),
  ('stochastic', 0.011491393465665557),
  ('descent', 0.01053788694709844),
  ('rate', 0.009427969079292447),
  ('objective', 0.009044526284691129),
  ('show', 0.008743000509709133),
  ('paper', 0.00728675499728591),
  ('result', 0.006284884589465521),
  ('iteration', 0.006138723797466128),
  ('proposed', 0.006024407001071116),
  ('local', 0.005867306536694031)],
 [('method', 0.04251922278205226),
  ('function', 0.03714214025593),
  ('algorithm', 0.036514995972270016),
  ('problem', 0.02489915213952075),
  ('gradient', 0.02240237557927833),
  ('optimization', 0.020453542798343653),
  ('convergence', 0.016402736289259798

In [17]:
ldaseq.print_topic_times(topic=1)

[[('algorithm', 0.023964009191690543),
  ('problem', 0.023929039796840468),
  ('policy', 0.016762517529938323),
  ('learning', 0.015611155917657478),
  ('state', 0.01179478987417689),
  ('function', 0.011585756577039613),
  ('show', 0.01049761602645038),
  ('decision', 0.00927663221753199),
  ('approach', 0.009235429202333143),
  ('optimal', 0.008481203523171393),
  ('action', 0.008084794221115287),
  ('value', 0.008010614443534085),
  ('game', 0.007254039308250083),
  ('agent', 0.0071452574720979245),
  ('reinforcement', 0.0069583411816164014),
  ('reward', 0.00684506668696176),
  ('solution', 0.006546464884172824),
  ('result', 0.005715886403601156),
  ('approximation', 0.005611211004850549),
  ('control', 0.00540862882703116)],
 [('algorithm', 0.02402950095170479),
  ('problem', 0.023995114749336337),
  ('policy', 0.016801210913199343),
  ('learning', 0.015645681715943084),
  ('state', 0.011818126617173288),
  ('function', 0.011608377345834392),
  ('show', 0.010517076333866698),
  (

In [18]:
ldaseq.print_topic_times(topic=2)

[[('network', 0.07489264796187334),
  ('neural', 0.019432276799098144),
  ('deep', 0.016006538036732625),
  ('model', 0.015218975195729227),
  ('input', 0.015114109686873267),
  ('learning', 0.014481216125465279),
  ('layer', 0.013012101921109742),
  ('architecture', 0.011489024994968428),
  ('training', 0.011043951346361935),
  ('memory', 0.009538760336443946),
  ('show', 0.008179441585826692),
  ('convolutional', 0.007993612946994364),
  ('task', 0.007640112801918682),
  ('recurrent', 0.007382954946923417),
  ('performance', 0.007037577052763307),
  ('sequence', 0.006383544822214452),
  ('unit', 0.006032842547848117),
  ('weight', 0.005818151407715588),
  ('using', 0.005815768120468781),
  ('system', 0.0057111516701710925)],
 [('network', 0.0752497303571573),
  ('neural', 0.019287580027527843),
  ('deep', 0.016113480456635774),
  ('model', 0.015199410301784514),
  ('input', 0.014954932122638594),
  ('learning', 0.01451829703453304),
  ('layer', 0.013085324615490267),
  ('architecture

In [19]:
ldaseq.print_topic_times(topic=3)

[[('model', 0.040827253499312786),
  ('inference', 0.019644474732730205),
  ('method', 0.01762729878109279),
  ('process', 0.014170397855711078),
  ('data', 0.013330403251752013),
  ('distribution', 0.012911203904778427),
  ('bayesian', 0.01237225662516763),
  ('approach', 0.012098207377850377),
  ('algorithm', 0.010440966656617414),
  ('variable', 0.00859400374948307),
  ('gaussian', 0.008321415046711727),
  ('parameter', 0.007562637497325342),
  ('using', 0.007269953193155606),
  ('variational', 0.0070631438404659165),
  ('prior', 0.0068282576757852905),
  ('probabilistic', 0.0068142143148496835),
  ('mixture', 0.006520273541954272),
  ('show', 0.006208828916869004),
  ('posterior', 0.006187365744038287),
  ('sampling', 0.0061379626892455715)],
 [('model', 0.040872184522202225),
  ('inference', 0.019705245312536673),
  ('method', 0.0176784747772652),
  ('process', 0.014168645046407824),
  ('data', 0.013364067234343514),
  ('distribution', 0.012942833682642653),
  ('bayesian', 0.01240

In [20]:
ldaseq.print_topic_times(topic=4)

[[('algorithm', 0.048990033497229156),
  ('learning', 0.02263743784442995),
  ('problem', 0.01538940941319631),
  ('online', 0.014680759874559402),
  ('clustering', 0.01209078000306836),
  ('regret', 0.01018401834965525),
  ('data', 0.008596643138691453),
  ('time', 0.008441224420088706),
  ('setting', 0.008327531885860726),
  ('bound', 0.007932101967008505),
  ('ranking', 0.007822475093649806),
  ('show', 0.007652778272486761),
  ('number', 0.0073163686555164096),
  ('active', 0.007149355804915227),
  ('query', 0.006627149790466053),
  ('cluster', 0.0063984524119674),
  ('label', 0.006085445143728217),
  ('set', 0.00587524841830823),
  ('result', 0.005354098080888689),
  ('user', 0.005274839437963061)],
 [('algorithm', 0.04915668064862554),
  ('learning', 0.022694810630985194),
  ('problem', 0.0154239542623036),
  ('online', 0.014712578613906421),
  ('clustering', 0.01211461427865518),
  ('regret', 0.010202472387672142),
  ('data', 0.00861052163514996),
  ('time', 0.008454996446703314

In [21]:
ldaseq.print_topic_times(topic=5)

[[('bound', 0.018514676963500242),
  ('distribution', 0.016262996727329365),
  ('function', 0.011829400488858274),
  ('sample', 0.010208312597908286),
  ('kernel', 0.009632134439725578),
  ('result', 0.00952250884385463),
  ('learning', 0.008597002198697079),
  ('show', 0.008591388894643002),
  ('error', 0.00855109536630168),
  ('probability', 0.00800618415813542),
  ('data', 0.007525295518071173),
  ('estimator', 0.007018323951063596),
  ('rate', 0.006724844997677313),
  ('analysis', 0.006490355665824607),
  ('complexity', 0.006410113302153385),
  ('graph', 0.006291961786116519),
  ('measure', 0.006244008710148105),
  ('class', 0.006165014731189272),
  ('random', 0.006001083716239742),
  ('test', 0.005964295332997329)],
 [('bound', 0.018561214817890352),
  ('distribution', 0.016302728902197295),
  ('function', 0.011854551180818107),
  ('sample', 0.01022791287295273),
  ('kernel', 0.009650232971673842),
  ('result', 0.009540453268116816),
  ('learning', 0.008612516188274046),
  ('show'

In [22]:
ldaseq.print_topic_times(topic=6)

[[('model', 0.021740693734603293),
  ('neuron', 0.013148007227565341),
  ('neural', 0.01307729931616488),
  ('stimulus', 0.010926613252837357),
  ('activity', 0.009958044576229123),
  ('response', 0.009684629279737011),
  ('brain', 0.008964495328106652),
  ('spike', 0.008868321141363402),
  ('information', 0.00779735152022385),
  ('data', 0.007549025785713903),
  ('signal', 0.007066693460717132),
  ('dynamic', 0.006782874352974177),
  ('show', 0.006541072746932624),
  ('system', 0.006253902478231464),
  ('population', 0.0061124050463462745),
  ('time', 0.005732963279190521),
  ('pattern', 0.005546472303432974),
  ('visual', 0.005424004468396624),
  ('functional', 0.005013720172018068),
  ('sensory', 0.0048739703440492345)],
 [('model', 0.02178474341157388),
  ('neuron', 0.013197360172975629),
  ('neural', 0.013065801118334658),
  ('stimulus', 0.010962596472125021),
  ('activity', 0.009988490530225111),
  ('response', 0.009713866746459302),
  ('brain', 0.008990385805607333),
  ('spike',

In [23]:
ldaseq.print_topic_times(topic=7)

[[('image', 0.026698897418786144),
  ('learning', 0.021991157988397965),
  ('feature', 0.019689156792553036),
  ('method', 0.014827418427993592),
  ('task', 0.01419998351023179),
  ('data', 0.013907120975548271),
  ('object', 0.012638859923393638),
  ('approach', 0.012579334197085823),
  ('classification', 0.01054164345584291),
  ('training', 0.00871836562478249),
  ('problem', 0.007141064704201788),
  ('set', 0.00694005671730046),
  ('classifier', 0.006301870501620461),
  ('using', 0.006186456720524049),
  ('show', 0.005942793403271101),
  ('kernel', 0.005933991555269678),
  ('performance', 0.0059091133584232005),
  ('propose', 0.005401440400556363),
  ('result', 0.005123144926935679),
  ('paper', 0.005097094948846551)],
 [('image', 0.026537974350701297),
  ('learning', 0.02207752128113075),
  ('feature', 0.019776777709046775),
  ('method', 0.014881432430623662),
  ('task', 0.014250652436269698),
  ('data', 0.01395604440457857),
  ('approach', 0.012621392494697726),
  ('object', 0.012

In [24]:
ldaseq.print_topic_times(topic=8)

[[('model', 0.053371804608957324),
  ('data', 0.015948462804085427),
  ('human', 0.012580506719482866),
  ('latent', 0.011195883938711388),
  ('structure', 0.010168559923722929),
  ('topic', 0.009704430118694882),
  ('word', 0.00939556648726721),
  ('learning', 0.007638849626997776),
  ('document', 0.0076018447059163176),
  ('representation', 0.006158142948354009),
  ('two', 0.0058724063426356995),
  ('show', 0.005795830714067815),
  ('approach', 0.005467508257761397),
  ('using', 0.005275675993685743),
  ('language', 0.005053589895859928),
  ('learn', 0.005014818485229545),
  ('experiment', 0.004928206772183126),
  ('different', 0.0047504375932141294),
  ('variable', 0.004716740853014925),
  ('task', 0.004658776021787705)],
 [('model', 0.05356043301128935),
  ('data', 0.015985393845814076),
  ('human', 0.012606526944322119),
  ('latent', 0.01121767353212662),
  ('structure', 0.010186346367763678),
  ('topic', 0.009722356853210644),
  ('word', 0.00941226206717112),
  ('learning', 0.007

In [25]:
ldaseq.print_topic_times(topic=9)

[[('algorithm', 0.01935101588160554),
  ('problem', 0.019310210031580868),
  ('matrix', 0.01724263855076564),
  ('data', 0.016372937241284257),
  ('sparse', 0.016109363821695803),
  ('method', 0.015172666773746957),
  ('linear', 0.009564051020429468),
  ('show', 0.007734388423469091),
  ('regression', 0.007184642420418882),
  ('analysis', 0.0066796131878662365),
  ('regularization', 0.006586697920347001),
  ('paper', 0.006052339279644078),
  ('result', 0.006015632731588376),
  ('norm', 0.005841668934800836),
  ('sparsity', 0.005610700236159323),
  ('number', 0.005525749803392345),
  ('using', 0.0054375866252519365),
  ('propose', 0.005180498891243888),
  ('proposed', 0.005056404079247624),
  ('vector', 0.0049383757946240055)],
 [('problem', 0.019368652231962782),
  ('algorithm', 0.019309370069437396),
  ('matrix', 0.01729138343804099),
  ('data', 0.016419990871570565),
  ('sparse', 0.016154951700744265),
  ('method', 0.015214167269098217),
  ('linear', 0.00958461489308007),
  ('show', 

In [26]:
# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[2.21729490e-04 2.21729490e-04 2.21729490e-04 2.02287887e-01
 2.21729490e-04 1.06372965e-01 1.79129860e-01 2.21729490e-04
 5.10878911e-01 2.21729490e-04]


In [27]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [28]:
ldaseq.print_topic_times(1) # evolution of values for first time slice


[[('algorithm', 0.023964009191690543),
  ('problem', 0.023929039796840468),
  ('policy', 0.016762517529938323),
  ('learning', 0.015611155917657478),
  ('state', 0.01179478987417689),
  ('function', 0.011585756577039613),
  ('show', 0.01049761602645038),
  ('decision', 0.00927663221753199),
  ('approach', 0.009235429202333143),
  ('optimal', 0.008481203523171393),
  ('action', 0.008084794221115287),
  ('value', 0.008010614443534085),
  ('game', 0.007254039308250083),
  ('agent', 0.0071452574720979245),
  ('reinforcement', 0.0069583411816164014),
  ('reward', 0.00684506668696176),
  ('solution', 0.006546464884172824),
  ('result', 0.005715886403601156),
  ('approximation', 0.005611211004850549),
  ('control', 0.00540862882703116)],
 [('algorithm', 0.02402950095170479),
  ('problem', 0.023995114749336337),
  ('policy', 0.016801210913199343),
  ('learning', 0.015645681715943084),
  ('state', 0.011818126617173288),
  ('function', 0.011608377345834392),
  ('show', 0.010517076333866698),
  (

In [29]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.8951134189377492
CV1 0.4359957737932568
U_Mass2 -1.877946053330016
CV2 0.4325845975043318
U_Mass3 -1.877081618748933
CV3 0.43505065291183576
U_Mass4 -1.9138948620996241
CV4 0.4271174444933764
U_Mass5 -1.9236896632867588
CV5 0.42803910939404605
U_Mass6 -1.910872039308845
CV6 0.42407539629150015
U_Mass7 -1.9042168226055385
CV7 0.43287244896327637
U_Mass8 -1.914025990033736
CV8 0.4267507334096396
U_Mass9 -1.8921440881354559
CV9 0.4240298762816471
U_Mass10 -1.8740596960402467
CV10 0.4304766781772911
U_Mass11 -1.8417576334133146
CV11 0.42977481842413845
U_Mass12 -1.8394304213546846
CV12 0.43175928199530345


In [30]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/